In [2]:
import pandas as pd
import requests
import base64
from concurrent.futures import ThreadPoolExecutor
from essentia.standard import (
    MonoLoader, TensorflowPredictEffnetDiscogs,
    TensorflowPredict2D, TempoCNN
)
import os
from pydub import AudioSegment

# Convert MP3 to WAV
def convert_mp3_to_wav(mp3_file, wav_file):
    audio = AudioSegment.from_mp3(mp3_file)
    audio.export(wav_file, format="wav")

# Function to calculate word similarity
def word_similarity(title1, title2):
    words1 = set(title1.lower().split())
    words2 = set(title2.lower().split())
    common_words = words1.intersection(words2)
    return len(common_words) / max(len(words1), len(words2))

# Function to download mp3 from link
def download_preview(preview_url, filename="preview.mp3"):
        """Descarga la vista previa de una canción si está disponible."""
        if not preview_url:
            raise Exception("No hay vista previa disponible para esta canción.")
        response = requests.get(preview_url)
        if response.status_code == 200:
            with open(filename, "wb") as file:
                file.write(response.content)
        else:
            raise Exception(f"Error al descargar la vista previa: {response.status_code} - {response.text}")

def extract_features(audio_file):
    try:
        audio = MonoLoader(filename=audio_file, sampleRate=16000, resampleQuality=4)()
        
        embedding_model = TensorflowPredictEffnetDiscogs(
            graphFilename="discogs-effnet-bs64-1.pb",
            output="PartitionedCall:1"
        )
        embeddings = embedding_model(audio)
        
        model_tempo = TempoCNN(graphFilename="deepsquare-k16-3.pb")
        global_tempo, local_tempo, local_tempo_probabilities = model_tempo(audio)
        
        model_genre = TensorflowPredict2D(graphFilename="mtg_jamendo_genre-discogs-effnet-1.pb")
        predictions_genre = model_genre(embeddings)
        
        model_instruments = TensorflowPredict2D(graphFilename="mtg_jamendo_instrument-discogs-effnet-1.pb")
        predictions_instruments = model_instruments(embeddings)
        
        model_mood = TensorflowPredict2D(graphFilename="mtg_jamendo_moodtheme-discogs-effnet-1.pb")
        predictions_mood = model_mood(embeddings)
        
        return {
            "tempo": global_tempo,
            "genre": predictions_genre.tolist(),
            "instruments": predictions_instruments.tolist(),
            "mood": predictions_mood.tolist()
        }
    except Exception as e:
        print(f"Error extracting features: {e}")
        return {
            "tempo": None,
            "genre": None,
            "instruments": None,
            "mood": None
        }
    
# Función para procesar una sola canción
def process_song(song):
    try:
        # Descargar el preview
        download_preview(song['preview_url'])

        # Convertir MP3 a WAV
        convert_mp3_to_wav("preview.mp3", "preview.wav")

        # Extraer características
        features = extract_features("preview.wav")

        # Calcular similitud de títulos
        title_confidence = word_similarity(song['title'], song['search_title'])

        # Retornar el resultado como un diccionario
        return {
            "title": song['title'],
            "artist_name": song['artist_name'],
            "title_confidence": title_confidence,
            "tempo": features["tempo"],
            "genre": features["genre"],
            "instruments": features["instruments"],
            "mood": features["mood"]
        }
    except Exception as e:
        print(f"Error procesando la canción '{song['title']}': {e}")
        return None  # Si hay un error, devolver None

2024-12-05 00:12:35.408062: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2024-12-05 00:12:35.408208: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
[   INFO   ] MusicExtractorSVM: no classifier models were configured by default
2024-12-05 00:12:44.288080: I tensorflow/core/platform/cpu_feature_guard.cc:142] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE3 SSE4.1 SSE4.2
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-12-05 00:12:44.297892: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcuda.so.1'; dlerror: libcuda.so.1: cannot open shared

In [ ]:
import os
import pandas as pd

# Cargar el archivo CSV
file_path = "output_with_search_columns_improved.csv"  # Cambia esto por tu ruta real
df = pd.read_csv(file_path).head(5)

# Procesar en lotes de 100
batch_size = 100
results = []

for i in range(0, len(df), batch_size):
    batch = df.iloc[i:i + batch_size]
    for song in batch.to_dict(orient="records"):
        result = process_song(song)
        if result:  # Agregar resultados válidos
            results.append(result)

# Crear un nuevo DataFrame con los resultados
results_df = pd.DataFrame(results)

# Guardar el DataFrame en un archivo CSV si es necesario
results_df.to_csv("processed_songs_with_features.csv", index=False)

In [3]:
import os
# Cargar el archivo CSV
file_path = "output_with_search_columns_improved.csv"  # Cambia esto por tu ruta real
df = pd.read_csv(file_path)

# Configuración del procesamiento por lotes
batch_size = 200
processed_folder = "processed"

# Crear la carpeta "processed" si no existe
os.makedirs(processed_folder, exist_ok=True)

# Identificar el último lote procesado
existing_files = [f for f in os.listdir(processed_folder) if f.startswith("processed_songs_with_features_")]
processed_batches = sorted(
    [int(f.split('_')[-1].replace('.csv', '')) for f in existing_files if f.split('_')[-1].replace('.csv', '').isdigit()]
)
last_batch_number = processed_batches[-1] if processed_batches else -1

# Procesar los lotes restantes
for batch_number, i in enumerate(range((last_batch_number + 1) * batch_size, len(df), batch_size), start=last_batch_number + 1):
    batch = df.iloc[i:i + batch_size]
    results = []

    for song in batch.to_dict(orient="records"):
        result = process_song(song)  # Asegúrate de tener implementada la función process_song
        if result:  # Agregar resultados válidos
            results.append(result)
            if ((len(results)/batch_size)*100 % 10 == 0):
                print((len(results)/batch_size)*100)

    # Crear un nuevo DataFrame con los resultados
    results_df = pd.DataFrame(results)

    # Guardar los resultados del lote actual
    batch_file_path = os.path.join(processed_folder, f"processed_songs_with_features_{batch_number}.csv")
    results_df.to_csv(batch_file_path, index=False)

    print(f"Lote {batch_number} procesado y guardado en {batch_file_path}")


[   INFO   ] TensorflowPredict: Successfully loaded graph file: `discogs-effnet-bs64-1.pb`
2024-12-05 00:13:43.980192: I tensorflow/core/platform/profile_utils/cpu_utils.cc:114] CPU Frequency: 2807995000 Hz
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `deepsquare-k16-3.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_genre-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_genre-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_instrument-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_instrument-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_moodtheme-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_moodtheme-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `

10.0


[   INFO   ] TensorflowPredict: Successfully loaded graph file: `discogs-effnet-bs64-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `deepsquare-k16-3.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_genre-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_genre-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_instrument-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_instrument-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_moodtheme-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_moodtheme-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `discogs-effnet-bs64-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `deepsquare-k16-3.pb`
[   

20.0


[   INFO   ] TensorflowPredict: Successfully loaded graph file: `discogs-effnet-bs64-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `deepsquare-k16-3.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_genre-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_genre-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_instrument-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_instrument-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_moodtheme-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_moodtheme-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `discogs-effnet-bs64-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `deepsquare-k16-3.pb`
[   

...

80.0


[   INFO   ] TensorflowPredict: Successfully loaded graph file: `discogs-effnet-bs64-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `deepsquare-k16-3.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_genre-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_genre-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_instrument-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_instrument-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_moodtheme-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_moodtheme-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `discogs-effnet-bs64-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `deepsquare-k16-3.pb`
[   

90.0


[   INFO   ] TensorflowPredict: Successfully loaded graph file: `discogs-effnet-bs64-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `deepsquare-k16-3.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_genre-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_genre-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_instrument-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_instrument-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_moodtheme-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `mtg_jamendo_moodtheme-discogs-effnet-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `discogs-effnet-bs64-1.pb`
[   INFO   ] TensorflowPredict: Successfully loaded graph file: `deepsquare-k16-3.pb`
[   

100.0
Lote 49 procesado y guardado en processed/processed_songs_with_features_49.csv
